In [340]:
from bs4 import BeautifulSoup as bs
from selenium import webdriver
import time, os, re
import pickle

In [251]:
# jobs = {}

In [341]:
path = "https://www.linkedin.com/jobs-guest/jobs/api/jobPosting/"

In [342]:
title_pattern = "(?:data scientist|data science|machine learning)"

In [343]:
def scrape(soup, job):
   title = soup.find("h2", {"class": "top-card-layout__title"})
   if title:
      title_text = title.get_text()
      job["title"] = title_text
   else:
      raise Exception("No job title")

   if not re.search(title_pattern, title_text, re.IGNORECASE):
      return job, (job['id'], "irrelevant listing", title_text)

   description = soup.find("div", {"class": "description__text"})
   if description:
      job["description"] = description
   else:
      raise Exception("No description text")

   companyInfo = soup.find("div", {"class": "topcard__flavor-row"})
   if companyInfo:
      job["companyInfo"] = companyInfo.get_text("|", strip=True)

   # job["soup"] = soup

   return job, None

In [344]:
def scrape_details(driver, url, job, job_id):
   driver.get(url)
   soup = bs(driver.page_source)

   try:
      job, error_message = scrape(soup, job)
   except Exception as e:
      print(f"Error scraping. Job id: {job_id}")
      return job, (job_id, "scraping", e)

   return job, error_message

In [345]:
def scrape_job_details(driver, job_ids, jobs):
   incomplete_scrapes = []
   already_scraped = []

   counter = 0

   for job_id in job_ids.keys() :
      if (job_id not in jobs):
         job = {}
         job['id'] = job_id

         url = path + job_id
         try:
            counter += 1
            time.sleep(1)
            job, incomplete_scrape = scrape_details(driver, url, job, job_id)
            if incomplete_scrape:
               incomplete_scrapes.append(incomplete_scrape)
            else:
               jobs[job_id] = job
         except Exception as e:
            incomplete_scrapes.append((job_id, "navigating", e))
      else:
         already_scraped.append(job_id)


      # if (counter > 5) & (counter%7 == 0):
      #    time.sleep(3)

   driver.quit()
   return jobs, incomplete_scrapes, already_scraped

In [352]:
with open('job_ids_linkedin_loads.pickle', 'rb') as handle:
   job_ids = pickle.load(handle)

job_ids

{'2908496770': None,
 '2912800721': None,
 '2911267267': None,
 '2911247709': None,
 '2909341435': None,
 '2911206168': None,
 '2912844894': None,
 '2911205495': None,
 '2912480226': None,
 '2911410386': None,
 '2909337839': None,
 '2912477964': None,
 '2911202175': None,
 '2912865535': None,
 '2910873146': None,
 '2911281499': None,
 '2912897584': None,
 '2911253200': None,
 '2909338218': None,
 '2912708341': None,
 '2911202739': None,
 '2910841361': None,
 '2908462198': None,
 '2911409783': None,
 '2906708941': None,
 '2905968184': None,
 '2912840985': None,
 '2841724223': None,
 '2908517430': None,
 '2908625109': None,
 '2901212301': None,
 '2911271258': None,
 '2904096931': None,
 '2909095938': None,
 '2906647334': None,
 '2912744296': None,
 '2904006446': None,
 '2906247368': None,
 '2911250669': None,
 '2911246147': None,
 '2911420967': None,
 '2911419822': None,
 '2909134730': None,
 '2902869759': None,
 '2904389147': None,
 '2906815029': None,
 '2906913218': None,
 '2910481507'

In [353]:
len(job_ids)

19261

In [354]:
chromedriver = "/Users/william.bell/opt/anaconda3/envs/metis/lib/python3.8/site-packages/chromedriver_binary/chromedriver"
os.environ["webdriver.chrome.driver"] = chromedriver
driver = webdriver.Chrome(chromedriver)
driver.implicitly_wait(3)

In [355]:
start = time.time()
cars, incomplete_scrapes, already_scraped = scrape_job_details(driver, job_ids, jobs)
end = time.time()
print(f"Time taken: {end - start}" )

Error scraping. Job id: 2818813990
Error scraping. Job id: 2846600085
Error scraping. Job id: 2813248263
Error scraping. Job id: 2850379794
Error scraping. Job id: 2781409061
Error scraping. Job id: 2886231919
Error scraping. Job id: 2884121457
Error scraping. Job id: 2901897434
Error scraping. Job id: 2889151740
Error scraping. Job id: 2894011244
Error scraping. Job id: 2916907915
Error scraping. Job id: 2914540762
Error scraping. Job id: 2903631433
Error scraping. Job id: 2893294047
Error scraping. Job id: 2913943604
Error scraping. Job id: 2918500894
Error scraping. Job id: 2916176285
Error scraping. Job id: 2823322181
Error scraping. Job id: 2821351616
Error scraping. Job id: 2914287577
Error scraping. Job id: 2913317532
Error scraping. Job id: 2911709397
Error scraping. Job id: 2884715925
Error scraping. Job id: 2916674209
Error scraping. Job id: 2861615760
Error scraping. Job id: 2903336355
Error scraping. Job id: 2912219442
Error scraping. Job id: 2773260648
Error scraping. Job 

In [349]:
incomplete_scrapes

[('2842730695', 'irrelevant listing', 'Engineer / Software Developer'),
 ('2871550487', 'irrelevant listing', 'Python Developer-Location Open'),
 ('2857494412', 'irrelevant listing', 'Software Developer - SQL Data Testing'),
 ('2916160821',
  'irrelevant listing',
  'Python Software Engineer, Commercial Systems'),
 ('2888869410', 'irrelevant listing', '2022 Intern - Software Engineer'),
 ('2905676144', 'irrelevant listing', 'Software Engineer - Data (Remote)'),
 ('2914944282', 'irrelevant listing', 'AWS Software Cloud Engineer'),
 ('2904632921',
  'irrelevant listing',
  'Software Engineer - Kubeflow/MLOps (Python/Kubernetes)'),
 ('2897398462', 'irrelevant listing', 'Software Developer '),
 ('2913278582', 'irrelevant listing', 'Software Engineer'),
 ('2881716387',
  'irrelevant listing',
  'Software Developer Associate (PowerShell)'),
 ('2891980866', 'irrelevant listing', 'SAP Application Developer'),
 ('2905031970', 'irrelevant listing', 'Junior Software Developer'),
 ('2885168239', '

In [356]:
len(incomplete_scrapes)

6488

In [357]:
len(already_scraped)

2628

In [358]:
len(jobs)

12777

In [265]:
jobs

{'2908496770': {'id': '2908496770',
  'description': <div class="description__text description__text--rich">
  <section class="show-more-less-html" data-max-lines="5">
  <div class="show-more-less-html__markup show-more-less-html__markup--clamp-after-5">
          I am looking for a self-motivated data scientist with machine learning experience. You will be working on a ground-breaking cloud R&amp;D platform designed to integrate the volumes of scientific resources, helping to build a digital workplace with direct impact on human health, pharmaceutical research and Life Sciences companies. This opportunity requires a strong technical background in machine learning; utilizing methods for understanding large scale biological data. <br/><br/>Responsibilities:<br/>•	Design and implement ML methods on proprietary and open-access datasets;<br/>•	Utilize large-scale datasets to generate statistically motivated research hypotheses;<br/>•	Apply statistical methods to rigorously test and evaluat

In [268]:
jobs['2908496770']['description'].get_text("|", strip=True)

'I am looking for a self-motivated data scientist with machine learning experience. You will be working on a ground-breaking cloud R&D platform designed to integrate the volumes of scientific resources, helping to build a digital workplace with direct impact on human health, pharmaceutical research and Life Sciences companies. This opportunity requires a strong technical background in machine learning; utilizing methods for understanding large scale biological data.|Responsibilities:|•\tDesign and implement ML methods on proprietary and open-access datasets;|•\tUtilize large-scale datasets to generate statistically motivated research hypotheses;|•\tApply statistical methods to rigorously test and evaluate research hypotheses;|•\tDevelop and foster external collaborations;|•\tProvide expert technical guidance and support customers in the design and analysis of experiments;|•\tWork both independently and as part of a collaborative team to develop data analysis and machine learning soluti

In [273]:
jobs['2911202739']['description']

<div class="description__text description__text--rich">
<section class="show-more-less-html" data-max-lines="5">
<div class="show-more-less-html__markup show-more-less-html__markup--clamp-after-5">
<p><strong>Overview</strong></p><p>We are seeking an expert in machine learning with a proven ability to develop and deploy predictive models to fill the position of Senior Data Scientist for the company. The core responsibility of this role is to design and implement highly accurate predictive models using state-of-the art ML technologies within a Python/R + AWS stack. Classification and regression with timeseries data will be the primary focus, and there will be opportunities to explore applications for unsupervised models, natural language processing, computer vision techniques, etc. The ideal candidate will combine technical expertise in predictive modeling with an understanding of MLOps, helping close the gap between model development and production.</p><p><br/></p><p>This is a full-tim

In [274]:
str(jobs['2905968184']['description'])

'<div class="description__text description__text--rich">\n<section class="show-more-less-html" data-max-lines="5">\n<div class="show-more-less-html__markup show-more-less-html__markup--clamp-after-5">\n<p><strong>About Us</strong></p><p>We are on a mission to revolutionize how work is done. Wilqo is a well-funded startup building an outcome-focused workflow optimization platform. We aren’t building to support status quo. We are building the future. We are growing fast and looking for smart, friendly, passionate people to join our team. If you are ready to challenge tradition, we are looking for you.</p><p><br/></p><p><strong>About the Position </strong></p><p>We are looking for a Data Scientist to help lead the implementation of advanced analytical concepts within our software.</p><ul><li>You will work closely with internal and external stakeholders to understand their business problems and communicate your findings</li><li>You will be challenged with minimizing the time stakeholders s

In [359]:
jobs_string_desc = {}

In [360]:
for key, value in jobs.items():
   value['description'] = str(value['description'])
   jobs_string_desc[key] = value

In [277]:
jobs_string_desc['2905968184']['description']

'<div class="description__text description__text--rich">\n<section class="show-more-less-html" data-max-lines="5">\n<div class="show-more-less-html__markup show-more-less-html__markup--clamp-after-5">\n<p><strong>About Us</strong></p><p>We are on a mission to revolutionize how work is done. Wilqo is a well-funded startup building an outcome-focused workflow optimization platform. We aren’t building to support status quo. We are building the future. We are growing fast and looking for smart, friendly, passionate people to join our team. If you are ready to challenge tradition, we are looking for you.</p><p><br/></p><p><strong>About the Position </strong></p><p>We are looking for a Data Scientist to help lead the implementation of advanced analytical concepts within our software.</p><ul><li>You will work closely with internal and external stakeholders to understand their business problems and communicate your findings</li><li>You will be challenged with minimizing the time stakeholders s

In [361]:
# with open('jobs_linkedin_loads.pickle', 'wb') as handle:
#    pickle.dump(jobs_string_desc, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [279]:
with open('jobs_linkedin_html.pickle', 'rb') as handle:
   unserialized_data = pickle.load(handle)

len(unserialized_data)

2596

In [281]:
unserialized_data['2908496770']['description']

'<div class="description__text description__text--rich">\n<section class="show-more-less-html" data-max-lines="5">\n<div class="show-more-less-html__markup show-more-less-html__markup--clamp-after-5">\n        I am looking for a self-motivated data scientist with machine learning experience. You will be working on a ground-breaking cloud R&amp;D platform designed to integrate the volumes of scientific resources, helping to build a digital workplace with direct impact on human health, pharmaceutical research and Life Sciences companies. This opportunity requires a strong technical background in machine learning; utilizing methods for understanding large scale biological data. <br/><br/>Responsibilities:<br/>•\tDesign and implement ML methods on proprietary and open-access datasets;<br/>•\tUtilize large-scale datasets to generate statistically motivated research hypotheses;<br/>•\tApply statistical methods to rigorously test and evaluate research hypotheses;<br/>•\tDevelop and foster ext

In [335]:
s = open('soup2.txt' , 'r')

In [336]:
b = bs(s)

In [337]:
j, e = scrape(b, {'id': '1234'})

In [338]:
j

{'id': '1234', 'title': 'Data '}

In [339]:
e

('1234', 'irrelevant listing', 'Data ')